## Libaries

In [1]:
# Main libraries installation
!pip install geopandas owslib requests contextily > nul


[notice] A new release of pip is available: 23.2.1 -> 23.3.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
# Import necessary libraries
from owslib.wfs import WebFeatureService  # For working with Web Feature Service
import geopandas as gpd  # For geospatial data manipulation and analysis
from shapely.geometry import Point, Polygon  # For handling geometric shapes
import pandas as pd  # For data manipulation and analysis
import os  # For operating system-related functionality
import io  # For input/output operations
import rasterio  # For reading and writing raster data
import numpy as np  # For numerical operations
from rasterio.crs import CRS  # For handling coordinate reference systems in raster data
import json  # For working with JSON data
import contextily as cx  # For basemaps and context tiles
import matplotlib.pyplot as plt  # For creating visualizations
import requests  # For making HTTP requests
from io import BytesIO  # For handling binary data
import zipfile  # For handling ZIP files
import pyproj  # For performing cartographic projections
import urllib.request  # For making URL requests
from urllib.error import ContentTooShortError  # For handling content too short errors during URL requests
import plotly.express as px  # For creating interactive visualizations
import warnings  # For managing warnings
warnings.filterwarnings("ignore")  # Ignore warnings during runtime

## Data Ingestion

In [3]:
# Define the WFS (Web Feature Service) URL and version
wfs_url = 'https://geoservicos.ibge.gov.br/geoserver/wfs'
ver = '1.1.0'

# Create a WebFeatureService object
wfs = WebFeatureService(url=wfs_url, version=ver)

# Get feature data from the WFS for the specified typename and coordinate reference system
response = wfs.getfeature(typename='CGEO:AmazoniaLegalLimites', srsname='EPSG:4674', outputFormat='application/json')
data = response.read()

# Load data into a dictionary
data = json.loads(data)

# Save data to a temporary GeoJSON file
with open('data/wfs_brasil/temp.geojson', 'w') as geojson_file:
    json.dump(data, geojson_file)

# Load data from the GeoJSON file into a GeoDataFrame
gdf = gpd.read_file('data/wfs_brasil/temp.geojson')

ERROR:fiona._env:PROJ: proj_create: no database context specified
ERROR:fiona._env:PROJ: proj_identify: C:\Program Files\PostgreSQL\15\share\contrib\postgis-3.3\proj\proj.db contains DATABASE.LAYOUT.VERSION.MINOR = 0 whereas a number >= 2 is expected. It comes from another PROJ installation.


## Data exploring

In [4]:
# Display information about the GeoDataFrame
gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 1 entries, 0 to 0
Data columns (total 7 columns):
 #   Column      Non-Null Count  Dtype   
---  ------      --------------  -----   
 0   id          1 non-null      object  
 1   OBJECTID    1 non-null      int64   
 2   amazonia__  1 non-null      object  
 3   FIRST_amaz  1 non-null      object  
 4   Shape_Leng  1 non-null      float64 
 5   Shape_Area  1 non-null      float64 
 6   geometry    1 non-null      geometry
dtypes: float64(2), geometry(1), int64(1), object(3)
memory usage: 184.0+ bytes


In [5]:
# Replace the value in the 'id' column
gdf['id'] = gdf['id'].replace({'AmazoniaLegalLimites.1': 'Amazonia Legal Limits'})

# Rename the 'id' column to 'name'
gdf = gdf.rename(columns={'id': 'name'})

In [6]:
# Display the first few rows of the GeoDataFrame
gdf.head()

name  OBJECTID amazonia__ FIRST_amaz  Shape_Leng  \
0  Amazonia Legal Limits         1        sim        sim     194.797   

   Shape_Area                                           geometry  
0     412.842  MULTIPOLYGON (((-43.99913 -2.39272, -43.99937 ...

In [7]:
# Print the original Coordinate Reference System (CRS) of the GeoDataFrame
print(gdf.crs)

GEOGCS["WGS 84",DATUM["WGS_1984",SPHEROID["WGS 84",6378137,298.257223563,AUTHORITY["EPSG","7030"]],AUTHORITY["EPSG","6326"]],PRIMEM["Greenwich",0,AUTHORITY["EPSG","8901"]],UNIT["degree",0.0174532925199433,AUTHORITY["EPSG","9122"]],AXIS["Latitude",NORTH],AXIS["Longitude",EAST],AUTHORITY["EPSG","4326"]]


In [8]:
# Reproject the GeoDataFrame to EPSG:4326
gdf=gdf.set_crs(4326, allow_override=True)

# Print the new Coordinate Reference System (CRS)
print(gdf.crs)

EPSG:4326


## Data Visualization

In [9]:
# Create a map using Plotly Express
fig = px.choropleth_mapbox(gdf, 
                           geojson=gdf.geometry, 
                           locations=gdf.index, 
                           color='name',
                           color_continuous_scale='inferno',
                           mapbox_style='open-street-map',
                           hover_name='name',  # Add 'name' as hover_name
                           center={'lat': gdf.geometry.centroid.y.mean(), 'lon': gdf.geometry.centroid.x.mean()},
                           zoom=3)

# Display the map
fig.update_layout(title='Amazonia Legal Limits from CGEO')
fig.show()